# Remapping the Lateral Boundary Data for ICON
---


This notebook serves as a template for the interpolation of lateral boundary data onto the limited area grid.  
The interpolation is performed by the `Climate Data Operators (CDO)`. 

The **CDO (Climate Data Operators)** are a collection of command-line operators to manipulate and analyze NetCDF and GRIB data. The CDO package is developed and maintained at the MPI for Meteorology in Hamburg. The CDO are also capable of remapping data to regular grids and triangular grids. Here, we will demonstrate how the CDO command-line tools can be used for the interpolation of the boundary datasets.

## Preparations

Internally, the CDOs make use of the ECCodes package for GRIB2 decoding/encoding:

In [ ]:
module load eccodes
export ECCODES_DEFINITION_PATH=/pool/data/ICON/ICON_training/eccodes/definitions.edzw-2.27.0-1:$ECCODES_DEFINITION_PATH

Then, we need to specify the input and output grid (the boundary grid):

In [ ]:
export INGRID="/scratch/${USER::1}/$USER/example_data/const/icon_grid_0026_R03B07_G.nc"  # grid for which the input data has been provided
export LOCALGRID="/pool/data/ICON/ICON_training/exercise_lam/grids/iconR3B08_DOM01.nc"   # this is the name (and path) of the destination grid (limited area grid)

The following command defines the output directory:

In [ ]:
# Create directory where the pre-processed input (initial and boundary data) for the LAM run is stored
export DATADIR_LAM=/scratch/${USER::1}/$USER/data_lam
mkdir -p ${DATADIR_LAM}

<div class="alert alert-success">
    <b style="color:#2d4b9b;">Exercise:</b> 
    </br>Define the absolute path of the raw forcing data from the example raw data set that has been discussed in <a href="../icon_exercise_prepare_lam.ipynb">icon_exercise_prepare_lam.ipynb</a>.<br/>
</div>

In [ ]:
export DATAPATH=???

<details>
<summary style="font-size: 1.1em;">Solution</summary>

`export DATAPATH="/scratch/${USER::1}/$USER/example_data/raw_data"`

</details>

Create a list of files which are contained in the forcing data directory `DATAPATH`.

In [ ]:
cd $DATAPATH
DATAFILES=`ls forcing_*.grb`

Identical to the remapping of initial data, the correct sub-grids need to be chosen and set:

In [ ]:
IGN=1
TGN=2

## Remapping

Now we can loop through the files and remap them to the target grid and change the file format to `NetCDF`.

<div class="alert alert-success">
    <b style="color:#2d4b9b;">Exercise:</b> 
    Perform the remapping.
</div>

In [ ]:
module load cdo

for DATAFILE in $DATAFILES
do
  # Replace .grb extension by .nc since we remap from grb to netcdf
  OUTFILE="$DATADIR_LAM/${DATAFILE%.*}_lbc.nc"
  # Perform remapping
  cdo -f nc2 remapcon,$LOCALGRID:$TGN -setgrid,$INGRID:$IGN $DATAFILE $OUTFILE.tmp
  # Change name of HHL field to ICON internal z_ifc (could also be changed in the latbc_varnames_map_file)
  cdo chname,HHL,z_ifc $OUTFILE.tmp $OUTFILE
  rm $OUTFILE.tmp
done

**Notes:**
- ICON supports reading boundary data on an auxiliary grid which contains only the cells of the boundary zone (Tutorial Section 2.3). While CDO is in capable of remapping to such an auxiliary grid, the generation of this grid file is not possible with CDO.
- Further details on boundary data remapping with CDO can be found in Section 2.3 of the tutorial.

<div class="alert alert-success">
    <b style="color:#2d4b9b;">Exercise:</b> 
    Why did we omit the explicit specifiaction of the fields for remapping?
</div>

<details>
<summary style="font-size: 1.1em;">Solution</summary>

The `pamore` call that was used to retrieve the data (see <a href="../icon_exercise_prepare_lam.ipynb">icon_exercise_prepare_lam.ipynb</a>) only retrieves the fields that are needed.

</details>

<div class="alert alert-success">
    <b style="color:#2d4b9b;">Exercise:</b> 
    The <code>cdo chname,HHL,z_ifc $OUTFILE.tmp $OUTFILE</code> in the above remapping script generates several warnings. Do you have an idea why?
</div>

<details>
<summary style="font-size: 1.1em;">Solution</summary>

The half-level height field `HHL` is only present in the first file. Since this is a constant field, ICON can reuse this information for subsequent lateral boundary files. `pamore` takes this into account when downloading a set of boundary data files.

</details>

<div class="alert alert-success">
    <b style="color:#2d4b9b;">Optional Exercise:</b> 
    The remapping of multiple files could be sped up significantly by precalculating the interpolation weightings. How could this be realized?
</div>

In [ ]:
module load cdo
...

<details>
<summary style="font-size: 1.1em;">Solution</summary>

```
module load cdo
export WEIGHTINGS="weightings.tmp.nc"

# Generate weightings
cdo -P 4 gencon,$LOCALGRID:$TGN -selgrid,$IGN $INGRID $WEIGHTINGS

for DATAFILE in $DATAFILES
do
  # Replace .grb extension by .nc since we remap from grb to netcdf
  OUTFILE="$DATADIR_LAM/${DATAFILE%.*}_lbc.nc"
  # Perform remapping
  cdo -f nc2 remap,$LOCALGRID:$TGN,$WEIGHTINGS  $DATAFILE $OUTFILE
  # Change name of HHL field to ICON internal z_ifc (could also be changed in the latbc_varnames_map_file)
  cdo chname,HHL,z_ifc $OUTFILE $OUTFILE
done

rm $WEIGHTINGS
```
</details>

**Note:** As pointed out in the ICON Tutorial, this workflow with precalculated weightings will fail when using the data in ICON due to missing values. 

## Further Reading and Resources

- **ICON Manual:** <a href="https://www.dwd.de/DE/leistungen/nwv_icon_tutorial/nwv_icon_tutorial.html">https://www.dwd.de/DE/leistungen/nwv_icon_tutorial/nwv_icon_tutorial.html</a>    <br/>A new <b>draft version</b> of the ICON Tutorial is available here: <a href="https://icon-training-2025-scripts-rendering-cc74a6.gitlab-pages.dkrz.de/index.html">https://icon-training-2025-scripts-rendering-cc74a6.gitlab-pages.dkrz.de/index.html</a>. It is currently being finalized and will be published soon.

---

*Author info: Deutscher Wetterdienst (DWD) 2025 ::  icon@dwd.de. For a full list of contributors, see CONTRIBUTING in the root directory. License info: see LICENSE file.*